# **Load Data**



In [1]:
import numpy as np

In [2]:
input_file = open('data.txt').readlines()
inp = []
for line in input_file:
  inp.append([int(x) for x in line.split()])
#inp = np.array(inp)
print(inp)

[[0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 42], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 45], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 47], [0, 0, 0, 49], [0, 0, 0, 49], [0, 0, 0, 49], [0

In [19]:
notes = set()
for arr in inp:
  notes = notes | set(arr)
num_notes = len(notes)
min_note = min(notes - {0})
print(min(notes - {0}),max(notes)) 

28 76


In [20]:
print(notes)

{0, 28, 30, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 76}


In [21]:
print(num_notes)

46


# **Sonifying Notes**

code taken from 
https://github.com/FlatAssembler/Notes-To-WAV-converter

In [16]:
from IPython.display import Audio

In [17]:
def notes_to_frequencies(notes):
    return 2 ** ((np.array(notes) - 69) / 12) * 440

def frequencies_to_samples(frequencies, tempo, sample_rate):
    note_duration = 60 / tempo 
    frequencies = np.round(note_duration * frequencies) / note_duration
    n_samples = int(note_duration * sample_rate)
    time = np.linspace(0, note_duration, n_samples)
    sine_waves = np.sin(2 * np.pi * frequencies.reshape(-1, 1) * time)
    sine_waves *= (frequencies > 9.).reshape(-1, 1)
    return sine_waves.reshape(-1)

def chords_to_samples(chords, tempo, sample_rate):
    freqs = notes_to_frequencies(chords)
    freqs = np.r_[freqs, freqs[-1:]] 
    merged = np.mean([frequencies_to_samples(melody, tempo, sample_rate)
                     for melody in freqs.T], axis=0)
    n_fade_out_samples = sample_rate * 60 // tempo 
    fade_out = np.linspace(1., 0., n_fade_out_samples)**2
    merged[-n_fade_out_samples:] *= fade_out
    return merged

def play_chords(chords, tempo=160, amplitude=0.1, sample_rate=44100, filepath=None):
    samples = amplitude * chords_to_samples(chords, tempo, sample_rate)
    if filepath:
        from scipy.io import wavfile
        samples = (2**15 * samples).astype(np.int16)
        wavfile.write(filepath, sample_rate, samples)
        return display(Audio(filepath))
    else:
        return display(Audio(samples, rate=sample_rate))

In [18]:
play_chords(inp[1700:1725])

# **Data Preprocessing**

- Input dims: [Batch_size, window_size, 1]
- Adding Embedding layer so that it captures relationship between notes
- Output dims: [Batch_size, window_size, 50]

In [ ]:
import tensorflow as tf

In [ ]:
def preprocess(window):
  window = tf.where(window == 0, window, window - min_note + 1)
  return window

In [ ]:
def batch_data(chorales,batch_size=32,window_size=32,window_shift=16):
  dataset = tf.data.Dataset.from_tensor_slices(chorales)
  dataset = dataset.window(window_size+1,window_shift,drop_remainder=True)
  dataset = dataset.flat_map(lambda window: window.batch(window_size*4)).map(preprocess)
  dataset = dataset.map(lambda window: tf.reshape(window, [-1])).map(lambda window: tf.expand_dims(window,(-1)))
  dataset = dataset.map(lambda window: (window[:-4],window[4:]))
  dataset = dataset.shuffle(1000)
  dataset = dataset.batch(batch_size)
  return dataset.prefetch(1)

In [104]:
train_dataset = batch_data(inp)

Cause: could not parse the source code of <function batch_data.<locals>.<lambda> at 0x7f8742257ae8>: found multiple definitions with identical signatures at the location. This error may be avoided by defining each lambda on a single line and with unique argument names.
Match 0:
(lambda window: tf.expand_dims(window, (- 1)))

Match 1:
(lambda window: tf.reshape(window, [(- 1)]))

To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Cause: could not parse the source code of <function batch_data.<locals>.<lambda> at 0x7f8742257ae8>: found multiple definitions with identical signatures at the location. This error may be avoided by defining each lambda on a single line and with unique argument names.
Match 0:
(lambda window: tf.expand_dims(window, (- 1)))

Match 1:
(lambda window: tf.reshape(window, [(- 1)]))

To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Cause: could not parse the source code of <funct

In [106]:
train_dataset

<PrefetchDataset shapes: ((None, None, 1), (None, None, 1)), types: (tf.int32, tf.int32)>

In [107]:
import keras

In [111]:
n_embedding_dims = 5

model = keras.models.Sequential([
    keras.layers.Embedding(input_dim=50, output_dim=n_embedding_dims,
                           input_shape=[None]),
    keras.layers.Conv1D(32, kernel_size=2, padding="causal", activation="relu"),
    keras.layers.BatchNormalization(),
    keras.layers.Conv1D(48, kernel_size=2, padding="causal", activation="relu", dilation_rate=2),
    keras.layers.BatchNormalization(),
    keras.layers.Conv1D(64, kernel_size=2, padding="causal", activation="relu", dilation_rate=4),
    keras.layers.BatchNormalization(),
    keras.layers.Conv1D(96, kernel_size=2, padding="causal", activation="relu", dilation_rate=8),
    keras.layers.BatchNormalization(),
    keras.layers.LSTM(256, return_sequences=True),
    keras.layers.Dense(50, activation="softmax")
])

model.summary()

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_3 (Embedding)      (None, None, 5)           250       
_________________________________________________________________
conv1d_12 (Conv1D)           (None, None, 32)          352       
_________________________________________________________________
batch_normalization_12 (Batc (None, None, 32)          128       
_________________________________________________________________
conv1d_13 (Conv1D)           (None, None, 48)          3120      
_________________________________________________________________
batch_normalization_13 (Batc (None, None, 48)          192       
_________________________________________________________________
conv1d_14 (Conv1D)           (None, None, 64)          6208      
_________________________________________________________________
batch_normalization_14 (Batc (None, None, 64)         

In [113]:
optimizer = keras.optimizers.Nadam(lr=1e-3)
model.compile(loss="sparse_categorical_crossentropy", optimizer=optimizer,
              metrics=["accuracy"])
model.fit(train_dataset, epochs=50)

Epoch 1/50
8/8 [==============================] - 9s 592ms/step - loss: 1.5404 - accuracy: 0.6182
Epoch 2/50
8/8 [==============================] - 5s 594ms/step - loss: 1.3418 - accuracy: 0.6767
Epoch 3/50
8/8 [==============================] - 5s 593ms/step - loss: 1.1478 - accuracy: 0.7281
Epoch 4/50
8/8 [==============================] - 5s 588ms/step - loss: 1.0332 - accuracy: 0.7585
Epoch 5/50
8/8 [==============================] - 5s 588ms/step - loss: 0.9338 - accuracy: 0.7800
Epoch 6/50
8/8 [==============================] - 5s 589ms/step - loss: 0.8787 - accuracy: 0.7933
Epoch 7/50
8/8 [==============================] - 5s 591ms/step - loss: 0.8104 - accuracy: 0.8055
Epoch 8/50
8/8 [==============================] - 5s 592ms/step - loss: 0.7576 - accuracy: 0.8139
Epoch 9/50
8/8 [==============================] - 5s 593ms/step - loss: 0.7330 - accuracy: 0.8174
Epoch 10/50
8/8 [==============================] - 5s 592ms/step - loss: 0.6899 - accuracy: 0.8239
Epoch 11/50
8/8 [==

In [116]:
model.save('model_bach_50epoch.h5')

# **Generating new notes**

In [231]:
def generate_notes(model, seed_notes, length):
  generated_chords = tf.reshape(seed_notes,[-1])
  for chord in range(length):
    next_notes = model.predict(seed_notes)
    next_notes = np.argmax(next_notes, axis=-1)[0:,-4:]
    generated_chords = tf.concat([generated_chords, tf.reshape(tf.constant(next_notes),[-1])],0)
    seed_notes = tf.concat([seed_notes[0,4:],next_notes.reshape(4,-1)], 0)
    seed_notes = tf.expand_dims(seed_notes,0)
  generated_chords = tf.where(generated_chords == 0, generated_chords, generated_chords + min_note - 1)
  return tf.reshape(generated_chords, shape=[-1,4])

In [235]:
start = np.random.randint(0,len(inp)-50,1)
seed_notes = inp[int(start):int(start)+32]
#print(seed_notes)
seed_notes = tf.constant(np.array(seed_notes))
seed_notes = preprocess(seed_notes)
seed_notes = tf.reshape(seed_notes,[-1])
seed_notes = tf.expand_dims(seed_notes, -1)
seed_notes = tf.expand_dims(seed_notes, 0)
#print(seed_notes)
#print(seed_notes.shape)
generated_notes = generate_notes(model,seed_notes,30)
print(generated_notes)

tf.Tensor(
[[69 54 54 45]
 [69 54 54 47]
 [69 54 54 47]
 [69 54 54 47]
 [69 54 54 47]
 [68 61 54 49]
 [68 61 54 49]
 [68 61 54 49]
 [68 61 54 49]
 [68 61 53 49]
 [68 61 53 49]
 [68 61 51 49]
 [68 61 51 49]
 [68 61 53 49]
 [68 61 53 49]
 [68 61 53 49]
 [68 61 53 49]
 [68 59 53 50]
 [68 59 53 50]
 [68 59 53 49]
 [68 59 53 49]
 [66 57 54 50]
 [66 57 54 50]
 [66 57 54 50]
 [66 57 54 50]
 [66 57 54 45]
 [66 57 54 45]
 [66 57 54 45]
 [66 57 54 45]
 [66 57 54 50]
 [66 57 54 50]
 [66 57 54 50]
 [66 66 66 48]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 66 66]], shape=(62, 4), dtype=int64)


In [236]:
play_chords(generated_notes.numpy(),amplitude=0.2)

# **Addition of randomness instead of picking the most prob. note**

In [254]:
def randomness(preds, temperature=1.0):
  preds = np.asarray(preds).astype('float64')
  preds = np.log(preds)/ temperature
  exp_preds = np.exp(preds)
  preds = exp_preds / np.sum(exp_preds)
  probabs = np.random.multinomial(1,preds,1)
  return np.argmax(probabs)

In [257]:
def generate_notes(model, seed_notes, length, temperature):
  generated_chords = tf.reshape(seed_notes,[-1])
  for chord in range(length):
    next_notes = model.predict(seed_notes)[0,-4:]
    next_notes_random = []
    for arr in next_notes:
      next_notes_random.append(randomness(arr,temperature))
    #next_notes = np.argmax(next_notes, axis=-1)[0:,-4:]
    next_notes = tf.constant(next_notes_random,dtype=tf.int64)
    generated_chords = tf.concat([generated_chords, next_notes],0)
    seed_notes = tf.concat([seed_notes[0,4:], tf.reshape(next_notes,[4,-1])], 0)
    seed_notes = tf.expand_dims(seed_notes,0)
  generated_chords = tf.where(generated_chords == 0, generated_chords, generated_chords + min_note - 1)
  return tf.reshape(generated_chords, shape=[-1,4])

In [258]:
start = np.random.randint(0,len(inp)-50,1)
seed_notes = inp[int(start):int(start)+32]
#print(seed_notes)
seed_notes = tf.constant(np.array(seed_notes))
seed_notes = preprocess(seed_notes)
seed_notes = tf.reshape(seed_notes,[-1])
seed_notes = tf.expand_dims(seed_notes, -1)
seed_notes = tf.expand_dims(seed_notes, 0)
#print(seed_notes)
#print(seed_notes.shape)
generated_notes = generate_notes(model,seed_notes,30,0.8)
print(generated_notes)

tf.Tensor(
[[ 0 57 54 30]
 [ 0 57 54 30]
 [ 0 57 49 30]
 [ 0 57 49 30]
 [ 0 57 49 30]
 [ 0 57 49 30]
 [ 0 57 50 30]
 [ 0 57 50 30]
 [ 0 57 50 30]
 [ 0 57 50 30]
 [ 0 57 50 42]
 [ 0 57 50 42]
 [ 0 57 50 42]
 [ 0 57 50 42]
 [ 0 59 50 44]
 [ 0 59 50 44]
 [ 0 59 50 44]
 [ 0 59 50 44]
 [ 0 59 47 44]
 [ 0 59 47 44]
 [ 0 59 47 44]
 [ 0 59 47 44]
 [ 0 59 52 44]
 [ 0 59 52 44]
 [ 0 59 52 44]
 [ 0 59 52 44]
 [ 0 59 52 42]
 [ 0 59 52 42]
 [ 0 59 52 44]
 [ 0 59 52 44]
 [ 0 61 52 45]
 [ 0 61 52 45]
 [66 66 66 66]
 [66 66 66 66]
 [66 66 64 66]
 [66 66 64 66]
 [66 66 66 65]
 [66 66 66 64]
 [66 66 64 64]
 [64 66 64 66]
 [64 66 64 66]
 [64 64 64 64]
 [64 64 66 64]
 [66 64 66 66]
 [66 64 66 66]
 [64 64 66 64]
 [64 64 64 64]
 [64 64 64 64]
 [66 64 66 66]
 [66 64 68 66]
 [66 64 64 66]
 [64 64 66 66]
 [64 64 66 66]
 [66 66 64 66]
 [64 69 64 64]
 [64 69 64 64]
 [64 69 66 48]
 [64 69 66 69]
 [64 68 66 69]
 [64 69 66 69]
 [64 66 66 69]
 [66 64 66 66]], shape=(62, 4), dtype=int64)


In [259]:
play_chords(generated_notes.numpy(),amplitude=0.2)

# **Practice**

In [22]:
import tensorflow as tf

In [70]:
tf.enable_eager_execution()

AttributeError: ignored

In [88]:
def preprocess(window):
  window = tf.where(window == 0, window, window - min_note + 1)
  return window

In [100]:
dataset = tf.data.Dataset.from_tensor_slices(inp)
dataset = dataset.window(33,16,drop_remainder=True)
dataset = dataset.flat_map(lambda window: window.batch(132)).map(preprocess)
dataset = dataset.map(lambda window: tf.reshape(window, [-1])).map(lambda window: tf.expand_dims(window,(-1)))
dataset = dataset.map(lambda window: (window[:-4],window[4:]))
dataset = dataset.shuffle(1000)
dataset = dataset.batch(1)
for X, y in dataset.take(1):
  print(X)
  print(y)


Cause: could not parse the source code of <function <lambda> at 0x7f873e26e0d0>: found multiple definitions with identical signatures at the location. This error may be avoided by defining each lambda on a single line and with unique argument names.
Match 0:
(lambda window: tf.expand_dims(window, (- 1)))

Match 1:
(lambda window: tf.reshape(window, [(- 1)]))

To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Cause: could not parse the source code of <function <lambda> at 0x7f873e26e0d0>: found multiple definitions with identical signatures at the location. This error may be avoided by defining each lambda on a single line and with unique argument names.
Match 0:
(lambda window: tf.expand_dims(window, (- 1)))

Match 1:
(lambda window: tf.reshape(window, [(- 1)]))

To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
tf.Tensor(
[[[ 0]
  [25]
  [ 0]
  [ 0]
  [ 0]
  [25]
  [ 0]
  [ 0]
  [ 0]
  [24]
  [ 0]


In [84]:
a = tf.constant([1,2,3,4,5,6])
a[:-2]

<tf.Tensor: shape=(4,), dtype=int32, numpy=array([1, 2, 3, 4], dtype=int32)>

In [87]:
a[1] = 5

TypeError: ignored

In [76]:
print(a)

tf.Tensor(
[[0 0 0 0]
 [0 0 0 0]], shape=(2, 4), dtype=int32)


In [78]:
print(a.numpy().reshape(-1))

[0 0 0 0 0 0 0 0]


In [30]:
data = tf.data.Dataset.range(100)
w = data.window(5,3)
#w = w.flat_map(lambda )

In [ ]:
dataset = tf.data.Dataset.range(7).window(2)
for window in dataset:
  print(list(window.as_numpy_iterator()))

[0, 1]
[2, 3]
[4, 5]
[6]


In [47]:
a = np.array([[1,2,3,4],[8,2,1,6]])
b = np.array([[5,6,7,8],[9,6,3,1]])
print(np.concatenate((a,b),1))

[[1 2 3 4 5 6 7 8]
 [8 2 1 6 9 6 3 1]]


In [45]:
a.shape

(4,)

In [ ]:
def batch_window(window):
  return window.batch(33)
def create_target(batch):
  X = batch[:,:-1]
  Y = batch[:,1:]
  return X, Y
dataset = tf.data.Dataset.from_tensor_slices(inp)
dataset = dataset.window(33,16,drop_remainder=True)
dataset = dataset.flat_map(batch_window)
dataset = dataset.shuffle(51)
dataset = dataset.batch(32)
dataset = dataset.map(create_target)
for i,arr in enumerate(dataset):
  if i>2:
    break
  print(arr)

In [ ]:
import tensorflow as tf

In [102]:
def preprocess(window):
  window = tf.where(window == 0, window, window - min_note + 1)
  return window

In [103]:
def batch_data(chorales,batch_size=32,window_size=32,window_shift=16):
  dataset = tf.data.Dataset.from_tensor_slices(chorales)
  dataset = dataset.window(window_size+1,window_shift,drop_remainder=True)
  dataset = dataset.flat_map(lambda window: window.batch(window_size*4)).map(preprocess)
  dataset = dataset.map(lambda window: tf.reshape(window, [-1])).map(lambda window: tf.expand_dims(window,(-1)))
  dataset = dataset.map(lambda window: (window[:-4],window[4:]))
  dataset = dataset.shuffle(1000)
  dataset = dataset.batch(batch_size)
  return dataset.prefetch(1)

In [ ]:
num_notes

46